In [3]:
import pyforest
from rdkit import Chem
from rdkit.Chem import AllChem

In [4]:
data_path = '../datasets/original_datasets/'

In [5]:
test = pd.read_csv(data_path+'NEK2_1_uM_min_50_pct_binding.csv')
test

<IPython.core.display.Javascript object>

target_name compound_id  \
0           NEK2      kdb_10   
1           NEK2     kdb_100   
2           NEK2    kdb_1003   
3           NEK2     kdb_101   
4           NEK2     kdb_102   
...          ...         ...   
1403        NEK2     kdb_976   
1404        NEK2      kdb_98   
1405        NEK2     kdb_980   
1406        NEK2     kdb_986   
1407        NEK2      kdb_99   

                                      base_rdkit_smiles  pct_binding  active  
0     CCS(=O)(=O)N1CC(CC#N)(n2cc(-c3ncnc4[nH]ccc34)c...     3.225806       0  
1     C[C@@H](Oc1cc(C(=O)Nc2ccc(C(=O)N3CCN(C)CC3)cc2...     3.225806       0  
2     CC1(O)CC(c2nc(-c3ccc4ccc(-c5ccccc5)nc4c3)c3c(N...     5.000000       0  
3     COCC(=O)NC/C=C/c1ccc2ncnc(Nc3ccc(Oc4ccc(C)nc4)...     6.158358       0  
4     COC(=O)c1ccc2c(c1)NC(=O)/C2=C(\Nc1ccc(N(C)C(=O...     6.158358       0  
...                                                 ...          ...     ...  
1403                       Oc1c2ccccc2c2c3c(cccc13)N=N2     9.090909       0  
1404  Cc1nc(Nc2n[nH]c3c2CN(C(=O)N[C@H](CN(C)C)c2cccc...     3.225806       0  
1405  Cc1cnc(-c2cnc(NCCNc3ccc(C#N)cn3)nc2-c2ccc(Cl)c...    85.000000       1  
1406            Nc1n[nH]c2nnc(-c3ccccc3)c(-c3ccccc3)c12     0.000000       0  
1407  C[C@@H](Oc1cc(-n2cnc3ccc(CN4CCN(C)CC4)cc32)sc1...    79.365079       1  

[1408 rows x 5 columns]

In [6]:
def check_labels(data_path, filename): 

  
    df = pd.read_csv(data_path+filename)

    pct_col = [col for col in df.columns if col.startswith('pct_')] 
    len(pct_col) == 1 
    pct_col = pct_col[0]
    invalid_labels = df[df['active']!= (df[pct_col]>=50).astype(int)]
    if invalid_labels.empty: 
        # print(f'correct label assignment based on {pct_col} column')
        pass
    else: 
        print(f'Error on label assignement.')
        print(invalid_labels)
    # check for duplicates here 
    duplicates = df[df.duplicated()]
    print(f'{df.shape}')
    #duplicates = df[df.duplicated(subset=['base_rdkit_smiles'])]
   
    if not duplicates.empty:
        print('Duplicate rows found:')
        print(duplicates)
        df_cleaned = df.drop_duplicates()
        print(f'df size original: {df.shape}')
        print(f'remove duplicates. {df_cleaned.shape}')
check_labels(data_path,'NEK2_1_uM_min_50_pct_inhibition.csv')

<IPython.core.display.Javascript object>

(2032, 5)


In [7]:
#create a dataset with folds

# must specify filename because the 50pct binding and inhibition files differ
# to-do: discuss how to do this --> this will create a file that is just this but with column specifying split
#       do we want to already integrate a split_uuid like AMPL? 
#       additionally, we still have to use the splits to create the "scaled df" 
def remove_duplicates(datapath, filename):
    df = pd.read_csv(f'{datapath}{filename}')
    duplicates = df.duplicated(subset=['base_rdkit_smiles'])
    if duplicates.any():
        print('Duplicate rows found:')
        print(df[duplicates])
        df_cleaned = df.drop_duplicates(subset=['base_rdkit_smiles'])
        print(f'df size original: {df.shape}')
        print(f'Removed duplicates. New df size: {df_cleaned.shape}')
    else: 
        df_cleaned = df
    return df_cleaned
    
def create_folds(datapath, filename, k_splits): 
    """filename: NEK#_1_uM_min_50_pct_(binding or inhibition).csv"""
    df = remove_duplicates(datapath, filename)
    # is this extra/too much and should we just assume what labels coincide with majority and minority? 
    # determine majority/minority class 
    #       AMPL takes in 'response column' 
    class_labels = df['active'].value_counts() 
    print(class_labels)
    if len(class_labels)>1: 
        majority_class_label =class_labels.idxmax() 
        majority_num = class_labels.max() 
        minority_class_label = class_labels.idxmin()
        minority_count = class_labels.min()
    df_majority = df[df['active']==majority_class_label]
    df_minority=df[df['active']==minority_class_label]
    # copy to avoid warnings 
    df_majority = df_majority.copy()
    df_minority = df_minority.copy()
    kf = KFold(k_splits,shuffle=True, random_state=42)
    # majority 
    for i, (_, v_ind) in enumerate(kf.split(df_majority)):
        df_majority.loc[df_majority.index[v_ind], 'fold'] = f"fold{i+1}"
    # minority 
    for i, (_, v_ind) in enumerate(kf.split(df_minority)):
        df_minority.loc[df_minority.index[v_ind], 'fold'] = f"fold{i+1}"
    all_fold_df = pd.concat([df_majority,df_minority])
    
    print(all_fold_df.shape)
    print(all_fold_df.active.value_counts())
    ## actually, this might be perfect jsut to save as "split df" because then 
    # in the next step of creating a dataset, you can choose what fold you want to be the test set 
    return all_fold_df
        
    

In [8]:
call in create_folds labeled with nek_folded 
    then call train_and__ to get full 80% train and do not touch 20% 
        then get 80% train and call create_folds
            then send to a seperate directory call K-fold 
    
in the the K-fold directory use the data that is folded called train___ 
    use to make train and test with each fold

SyntaxError: invalid syntax (2774517515.py, line 1)

In [9]:
def train_and__(data_path, fold_df, test_fold):
   """function to label 'train' or 'test' in the 'subset' column
   to be used to create train/test OR train/val
   fold_df: dataframe with column 'fold'
   test_fold (str): fold to make the test set (the remaining folds will be train)
   """
   df = pd.read_csv(data_path+fold_df) 
   df['subset'] = df['fold'].apply(lambda x: 'test' if x == test_fold else 'train')

   return df[['NEK','compound_id', 'active', 'base_rdkit_smiles', 'subset']]



In [10]:
def get_bind_inhib(df_name):
    match = re.search(r'_([^_]+)\.csv$',df_name)
    return match.group(1) if match else None
    # returns 'binding' or 'inhibition' 
og_dfs = [file for file in os.listdir(data_path) if file.startswith('NEK')]

for df in og_dfs: 
    folded_df = create_folds(data_path, df,5)
    bind_inhib = get_bind_inhib(df)
    nek_name = f'NEK{df[3]}_{bind_inhib}'
    print(nek_name)
    folded_df['NEK']=nek_name 
    folded_df.to_csv(f'../datasets/initial_fold/{nek_name}_initial_fold.csv',index=False)

    # folded_df.to_csv('intial_fold')

# def label_train_validation(data_path, train80df, fold)
#     return train df with folds

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

active
0    351
1     42
Name: count, dtype: int64


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

(1408, 6)
active
0    1351
1      57
Name: count, dtype: int64


<IPython.core.display.Javascript object>

NEK2_binding


In [11]:
neks = ['NEK2_binding', 'NEK2_inhibition', 'NEK3_binding', 'NEK5_binding','NEK9_binding','NEK9_inhibition']

for nek in neks:
    fold_df_name = nek+"_initial_fold.csv"
    print(fold_df_name)
    labeled_df = train_and__("/Users/radhi/Desktop/GitHub/atom2024/atom2024/notebooks/paper/datasets/initial_fold/" , fold_df_name, "fold1")
    labeled_df.to_csv(f'/Users/radhi/Desktop/GitHub/atom2024/atom2024/notebooks/paper/datasets/80train_20test/{nek}_80_20_df.csv',index=False)
#labeled_df
    



NEK2_binding_initial_fold.csv


<IPython.core.display.Javascript object>

NEK2_inhibition_initial_fold.csv


<IPython.core.display.Javascript object>

NEK3_binding_initial_fold.csv


...

<IPython.core.display.Javascript object>

NEK9_binding_initial_fold.csv


<IPython.core.display.Javascript object>

NEK9_inhibition_initial_fold.csv


<IPython.core.display.Javascript object>

In [12]:
#featurize 
def featurize(data_path, filename, feat_type, moe_path=None, moe_file=None, mfp_radius=2, nBits=2048): 
    if (feat_type == 'MOE') and (moe_path is not None) and (moe_file is not None): 
        df = create_moe(data_path, filename, moe_path, moe_file)
    elif feat_type == 'MFP': 
        df = create_mfp(data_path, filename, mfp_radius, nBits)
    
    return df


In [13]:
def create_moe(data_path, filename, moe_path, moe_file):
    """(intended use for already existing dataset)
    This function will use an existing dataframe with smiles column to
    get the features from an existing file (moe_path+moe_file) with the MOE features generated"""
    
    drop_cols = ['active', 'compound_id']
    df = remove_duplicates(data_path, filename)
    df=df.drop(columns=drop_cols)
    

    moe_df=remove_duplicates(moe_path,moe_file)
    

    final_df=moe_df.merge(df, how='outer', on=['base_rdkit_smiles'], suffixes=('_moe_desc', '_og'))
    id_cols = ['NEK', 'compound_id','base_rdkit_smiles','subset', 'active']
    feat_cols = set(list(final_df.columns))-set(id_cols)
    
    final_order_cols = list(id_cols)+list(feat_cols)


    return final_df[final_order_cols]
    # in production code , check for smiles col 

test_df = featurize('/Users/radhi/Desktop/GitHub/atom2024/atom2024/notebooks/paper/datasets/80train_20test/','NEK2_inhibition_80_20_df.csv', 'MOE','/Users/radhi/Desktop/GitHub/atom2024/atom2024/notebooks/paper/datasets/original_datasets/scaled_descriptors/' , 'NEK2_1_uM_min_50_pct_inhibition_with_moe_descriptors.csv')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Duplicate rows found:
     compound_id                                  base_rdkit_smiles  active  \
895     kdb_1014          Nc1nccc(-c2c(-c3ccc(F)cc3)ncn2C2CCNCC2)n1       0   
1056    kdb_3409  [O-][S+]1CCN(Cc2ccc(-c3ccc4ncnc(Nc5ccc(OCc6ccc...       0   
1060    kdb_3151  CCn1c(-c2nonc2N)nc2cnc(Oc3cccc(NC(=O)c4ccc(OCC...       0   
1142    kdb_3359  CN1CCC(C(=O)Nc2n[nH]c3nc(-c4ccc(O)cc4)c(Br)cc2...       0   
1357    kdb_3412  COc1ccc2cc(-c3c(-c4ccncc4)nc(-c4ccc([S+](C)[O-...       0   
1449    kdb_3208  COc1ccc2cc(-c3c(-c4ccncc4)nc(-c4ccc([S+](C)[O-...       0   
1561    kdb_3362  CCN1CCC(CC(=O)Nc2n[nH]c3nc(-c4cccs4)c(Br)cc23)CC1       0   
1694    kdb_2601                Fc1ccc(-c2nc3n(c2-c2ccncc2)CCS3)cc1       0   
1760    kdb_2432  Nc1ncnc2occ(-c3ccc(NC(=O)Nc4cc(C(F)(F)F)ccc4F)...       0   
1763    kdb_2231  [O-][S+]1CCN(Cc2ccc(-c3ccc4ncnc(Nc5ccc(OCc6ccc...       0   
1911    kdb_3411  [O-][S+]1CCN(Cc2ccc(-c3ccc4ncnc(Nc5ccc(OCc6ccc...       0   
2034    kdb_3410  CCN1CCC(CC(=

In [14]:
test_df

NEK compound_id  \
0     NEK2_inhibition     kdb_819   
1     NEK2_inhibition     kdb_952   
2     NEK2_inhibition     kdb_704   
3     NEK2_inhibition    kdb_1416   
4     NEK2_inhibition    kdb_3103   
...               ...         ...   
2027  NEK2_inhibition     kdb_688   
2028  NEK2_inhibition    kdb_3174   
2029  NEK2_inhibition     kdb_687   
2030  NEK2_inhibition    kdb_3568   
2031  NEK2_inhibition     kdb_875   

                                      base_rdkit_smiles subset  active  \
0                O=C1CCCN1Cc1ccc2c(c1)[nH]c(=O)c1cccn12   test       1   
1                         O=C1NCCc2[nH]c(-c3ccncc3)cc21   test       0   
2     CN(C)CC1CN(c2ccc3nc(-c4n[nH]c5ccc([N+](=O)[O-]...  train       0   
3       CC(C)Cc1nc(Nc2ccc(N3CCOCC3)c(Cl)c2)nc2[nH]ccc12  train       0   
4     O=C([O-])c1ccc(Oc2nccc(-c3c(-c4ccc(F)cc4)ncn3C...  train       0   
...                                                 ...    ...     ...   
2027  CC(C)(C)NC(=O)Nc1ccc2[nH]nc(-c3nc4ccc(N5CCC(N6...  train       0   
2028  CS(=O)(=O)CCNCc1ccc(-c2ccc3ncnc(Nc4ccc(OCc5ccc...  train       0   
2029        COCCOc1ccc2[nH]c(-c3n[nH]c4cc(F)ccc34)nc2c1   test       0   
2030          COc1cc(OC)c(/C=C2\C(=O)Nc3ccccc32)c(OC)c1  train       0   
2031       NC(=O)c1cccc2[nH]c(-c3ccc(C4CCCNC4)cc3F)nc12   test       0   

      vsurf_ID6  vsurf_D2_per_atom      h_pKb  a_base  SlogP_VSA1  ...  \
0      0.696768          12.729167  16.180479       0   33.551723  ...   
1      0.547527          13.217593   7.893939       0   22.044313  ...   
2      0.864357          10.179545   7.356675       1   40.534153  ...   
3      0.911796          11.708333   8.592092       0   51.581810  ...   
4      0.590558           9.399554   8.355978       1   53.719688  ...   
...         ...                ...        ...     ...         ...  ...   
2027   0.708769           9.857143   7.092664       1   56.289246  ...   
2028   1.209251          11.401119   9.870059       1   99.753494  ...   
2029   0.921758          11.573718   7.679154       0   33.448536  ...   
2030   1.125516           9.675000  14.000000       0   23.269535  ...   
2031   0.435739          10.527778   9.090064       1   22.044313  ...   

      chi0v_per_atom  petitjeanSC      dens  reactive  zagreb_per_atom  \
0           0.319540     1.000000  1.054108         0         3.277778   
1           0.320608     1.000000  1.050443         0         3.185185   
2           0.316063     1.000000  1.061813         1         3.127273   
3           0.321243     1.000000  1.038061         0         2.823529   
4           0.325456     1.000000  1.109522         0         3.250000   
...              ...          ...       ...       ...              ...   
2027        0.294225     0.909091  1.005236         0         2.753247   
2028        0.353803     0.916667  1.169420         0         3.074627   
2029        0.332492     0.875000  1.110914         0         3.333333   
2030        0.329361     0.833333  1.043005         0         3.000000   
2031        0.305733     0.857143  1.054838         0         3.022222   

      Q_VSA_NEG_per_atom  a_don  vsa_other  vsurf_ID1  chi1v_per_atom  
0               3.841707      1  25.899061   0.437240        0.197783  
1               2.657731      2  12.949531   0.447240        0.194407  
2               2.517581      4  45.121613   0.215018        0.186541  
3               3.049999      3  26.872137   0.728720        0.190392  
4               3.485693      0  59.443317   0.396274        0.197394  
...                  ...    ...        ...        ...             ...  
2027            2.800291      6  28.631105   0.425689        0.181727  
2028            4.381087      1  61.914673   0.688055        0.227738  
2029            3.049956      4  11.190562   0.268658        0.192287  
2030            2.730199      1  12.949531   0.759525        0.177516  
2031            3.058876      3  24.140093   0.250234        0.189616  

[2032 rows x 311 columns]

In [17]:
def smiles_to_fps(smiles_list, radius=2, nBits=2048):
    fps = []
    for smi in smiles_list:
        mol = Chem.MolFromSmiles(smi)
        if mol is not None:
            fp = AllChem.GetMorganFingerprintAsBitVect(mol, radius, nBits=nBits)
            arr = np.zeros((1,), dtype=np.int8)
            Chem.DataStructs.ConvertToNumpyArray(fp, arr)
            fps.append(arr)
    return np.array(fps)


def create_mfp(file_path, filename, mfp_radius, nBits):
    df = pd.read_csv(file_path+filename)

    id_data = df[['compound_id','base_rdkit_smiles', 'NEK','subset','active']]
    smiles = df['base_rdkit_smiles']

    mfp_feats = smiles_to_fps(smiles,mfp_radius,nBits)
    mfp_df = pd.DataFrame(mfp_feats)

    id_cols = ['NEK', 'compound_id','base_rdkit_smiles','subset', 'active']
    feat_cols = set(list(mfp_df.columns))-set(id_cols)
    final_order_cols = list(id_cols)+list(feat_cols)
    final_df = pd.concat([mfp_df, df],axis=1)
    final_df = final_df[final_order_cols]
    display(final_df)

    
    # testX_mfp_df['active'] = test_y.reset_index(drop=True)
    # final_df = pd.concat([trainX_mfp_df,testX_mfp_df], ignore_index=True)
    return final_df
        

test_df = featurize('/Users/radhi/Desktop/GitHub/atom2024/atom2024/notebooks/paper/datasets/80train_20test/','NEK2_inhibition_80_20_df.csv', 'MFP',2,2048 )

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

NEK compound_id  \
0     NEK2_inhibition    kdb_1000   
1     NEK2_inhibition    kdb_1001   
2     NEK2_inhibition    kdb_1003   
3     NEK2_inhibition    kdb_1004   
4     NEK2_inhibition    kdb_1005   
...               ...         ...   
2027  NEK2_inhibition     kdb_911   
2028  NEK2_inhibition     kdb_927   
2029  NEK2_inhibition     kdb_944   
2030  NEK2_inhibition     kdb_966   
2031  NEK2_inhibition     kdb_977   

                                      base_rdkit_smiles subset  active  0  1  \
0     Oc1ccc(-c2n[nH]c(Nc3cccc(Cl)c3)c2-c2ccc(O)cc2)cc1  train       0  0  0   
1           Nc1nonc1-n1nnc(C(=O)NN=Cc2cccs2)c1-c1ccccc1  train       0  0  0   
2     CC1(O)CC(c2nc(-c3ccc4ccc(-c5ccccc5)nc4c3)c3c(N...  train       0  0  0   
3              COc1ccc(C=C2C(=O)ON=C2c2ccc(Br)cc2)cc1OC  train       0  0  0   
4     CN(C)c1cccc2c(S(=O)(=O)N(CCN)c3cncc(-c4ccc5cnc...  train       0  0  0   
...                                                 ...    ...     ... .. ..   
2027  CCN(CC)CCNC(=O)C=Cc1cnc(N)c2c(-c3ccc(NC(=O)Nc4...  train       1  0  0   
2028  Cc1cccc(NC(=O)Nc2ccc(-c3cnc4c(-c5cnn(C)c5)cnn4...  train       1  0  0   
2029    O=C(NNC(=S)Nc1ccc(Cl)cc1)C(O)(c1ccccc1)c1ccccc1  train       1  0  0   
2030  O=C(Cc1ccccc1)Nc1cccc(-c2nc3sccn3c2-c2ccnc(Nc3...   test       1  0  0   
2031     O=C(NNC(=S)Nc1ccc(F)cc1)C(O)(c1ccccc1)c1ccccc1  train       1  0  0   

      2  3  4  ...  2038  2039  2040  2041  2042  2043  2044  2045  2046  2047  
0     0  0  0  ...     0     0     0     0     0     0     0     0     0     0  
1     0  0  0  ...     0     0     0     0     0     0     0     0     0     0  
2     0  0  0  ...     0     0     0     0     0     0     0     0     0     0  
3     0  0  0  ...     0     0     0     0     0     0     0     0     0     0  
4     0  0  0  ...     0     0     0     0     0     0     0     0     0     0  
...  .. .. ..  ...   ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  
2027  0  0  0  ...     0     0     0     0     0     0     0     0     0     0  
2028  0  0  0  ...     0     0     0     0     0     0     0     0     0     0  
2029  0  0  0  ...     0     0     0     0     0     0     0     0     0     0  
2030  0  0  0  ...     0     0     0     0     0     0     0     0     0     0  
2031  0  0  0  ...     0     0     0     0     0     0     0     0     0     0  

[2032 rows x 2053 columns]

In [20]:
og_df_path = '/Users/radhi/Desktop/GitHub/atom2024/atom2024/notebooks/paper/datasets/80train_20test/' 
scaled_desc_path = '/Users/radhi/Desktop/GitHub/atom2024/atom2024/notebooks/paper/datasets/original_datasets/scaled_descriptors/'
featurized_filepath = '/Users/radhi/Desktop/GitHub/atom2024/atom2024/notebooks/paper/datasets/80train_20test/featurized/' 
for nek in ['2','3','5','9']: 
    if nek in ['2','9']:
        bind_inhib = ['binding','inhibition']
    else: 
        bind_inhib = ['binding']
    for bi in bind_inhib: 

        for feat in ['MOE','MFP']: 
            print(f'NEK {nek} {bi} {feat}')
            og_df_name = f'NEK{nek}_{bi}_80_20_df.csv'
            if feat == 'MOE': 
                desc_filename =f'NEK{nek}_1_uM_min_50_pct_{bi}_with_moe_descriptors.csv'
                final_moe_df = featurize(og_df_path,og_df_name,feat,scaled_desc_path,desc_filename)
                final_moe_df.to_csv(f'{featurized_filepath}NEK{nek}_{bi}_{feat}_none.csv',index=False)
                
            elif feat=='MFP': 
                final_mfp_df = featurize(og_df_path,og_df_name,feat,2,2048)
                final_mfp_df.to_csv(f'{featurized_filepath}NEK{nek}_{bi}_{feat}_none.csv',index=False)



NEK 2 binding MOE


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

NEK 2 binding MFP


<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

NEK compound_id  \
0    NEK9_inhibition    kdb_1014   
1    NEK9_inhibition    kdb_1153   
2    NEK9_inhibition    kdb_1618   
3    NEK9_inhibition    kdb_2013   
4    NEK9_inhibition    kdb_2200   
..               ...         ...   
388  NEK9_inhibition    kdb_3769   
389  NEK9_inhibition    kdb_3771   
390  NEK9_inhibition    kdb_3772   
391  NEK9_inhibition    kdb_3774   
392  NEK9_inhibition    kdb_3775   

                                     base_rdkit_smiles subset  active  0  1  \
0            Nc1nccc(-c2c(-c3ccc(F)cc3)ncn2C2CCNCC2)n1  train       0  0  0   
1                  Cn1cc(C=C2C(=O)Nc3cccnc32)c2ccccc21  train       0  0  0   
2              COc1ccc(COc2ccc(Cc3cnc(N)nc3N)cc2OC)cc1  train       0  0  0   
3    NC(=O)c1ccc(-c2nc(-c3ccccn3)c(-c3ccc4c(c3)OCO4...   test       0  0  0   
4         c1ccc(Cc2nc3ccc(Nc4ncnc5ccccc45)cc3[nH]2)cc1  train       0  0  0   
..                                                 ...    ...     ... .. ..   
388  COc1cc(N2CCN(C)CC2)ccc1Nc1ncc2c(n1)n1c(cc3cccc...  train       1  0  0   
389  COc1cc(C(=O)N2CCC(N3CCN(C)CC3)CC2)ccc1Nc1ncc2c...  train       1  0  0   
390  CCOc1cc(N2CCC(O)CC2)ccc1Nc1ncc2c(n1)n1c(cc3ccc...   test       1  0  0   
391  COc1cc(N2CCOCC2)ccc1Nc1ncc2c(n1)N1c3ccccc3CC1C...  train       1  0  0   
392  CCn1c(=O)c2cc3ccccc3n2c2nc(Nc3ccc(N4CCN(C)CC4)...  train       1  0  0   

     2  3  4  ...  2038  2039  2040  2041  2042  2043  2044  2045  2046  2047  
0    0  0  0  ...     0     0     0     0     0     0     0     0     0     0  
1    0  0  0  ...     0     0     0     0     0     0     0     0     0     0  
2    0  0  0  ...     0     0     0     0     1     0     0     0     0     0  
3    0  0  0  ...     0     0     0     0     0     0     0     0     0     0  
4    0  0  0  ...     0     0     0     0     0     0     0     0     0     0  
..  .. .. ..  ...   ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  
388  0  0  0  ...     0     0     0     0     0     0     0     0     0     0  
389  0  0  0  ...     0     0     0     0     0     0     0     0     0     0  
390  0  0  0  ...     0     0     0     0     0     0     0     0     0     0  
391  0  0  0  ...     0     0     0     0     0     0     0     0     0     0  
392  0  0  0  ...     0     0     0     0     0     1     0     0     0     0  

[393 rows x 2053 columns]